# Broadcast

## But : Faire un broadcast, départ décalé 


### Informations générales

#### Le nom de l'expérience : Nom du folder contenant les fichiers sources et résultats

In [1]:
experiment_name = "Time_Bcast"
crashed = True

#### Versions

In [2]:
%%bash -s
git log -n 1
python3 --version
R --version

commit d28755a0ac2fbe9578a6f432611a8b35458459aa
Author: Najwa Ez Zine <nezzine@fnancy>
Date:   Wed Jul 4 23:37:36 2018 +0200

    Automatic results update : Time_Bcast --- None R tutorial
Python 3.5.3
R version 3.3.3 (2017-03-06) -- "Another Canoe"
Copyright (C) 2017 The R Foundation for Statistical Computing
Platform: x86_64-pc-linux-gnu (64-bit)

R is free software and comes with ABSOLUTELY NO WARRANTY.
You are welcome to redistribute it under the terms of the
GNU General Public License versions 2 or 3.
For more information about these matters see
http://www.gnu.org/licenses/.



### Préparation de l'environnement (FRONTEND)

#### Installation des modules

In [3]:
%%bash -s
pip3 install --user execo
pip3 install --user requests

# Permet affichage pllus lisible avec couleurs
pip3 install --user termcolor

# Permettent d'utiliser R :
pip3 install --user rpy2
pip3 install --user tzlocal

  Using cached https://files.pythonhosted.org/packages/65/47/7e02164a2a3db50ed6d8a6ab1d6d60b69c4c3fdf57a284257925dfc12bda/requests-2.19.1-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/bc/a9/01ffebfb562e4274b6487b4bb1ddec7ca55ec7510b22e4c51f14098443b8/chardet-3.0.4-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/bd/c9/6fdd990019071a4a32a5e7cb78a1d92c53851ef4f56f62a3486e6a7d8ffb/urllib3-1.23-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/4b/2a/0276479a4b3caeb8a8c1af2f8e4355746a97fab05a372e4a2c6a6b876165/idna-2.7-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/7c/e6/92ad559b7192d846975fc916b65f667c7b8c3a32bea7372340bfe9a15fa5/certifi-2018.4.16-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/7f/ff/ae64bacdfc95f27a016a7bed8e8686763ba4d277a78ca76f32659220a731/Jinja2-2.10-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/67/4b

#### Chargement des modules dans l'environnement

In [4]:
import execo
import math
import collections
import os
import sys
import json
import time
import random
import datetime
import re
import tzlocal

from execo import *
from execo_g5k import *
from execo_engine import *

from shutil import copy
from subprocess import check_output

from threading import Thread

from collections import deque, OrderedDict
from termcolor import *
from subprocess import *

#### Chargement de l'outil permettant l'utilisation de R

In [5]:
%load_ext rpy2.ipython

In [ ]:
%%R
install.packages('ggplot2')
install.packages('dplyr')
install.packages('tidyr')

/home/nezzine/.local/lib/python3.5/site-packages/rpy2/rinterface/__init__.py:146: RRuntimeWarning: Installing package into ‘/home/nezzine/R/x86_64-pc-linux-gnu-library/3.3’
(as ‘lib’ is unspecified)

  warnings.warn(x, RRuntimeWarning)


Selection: 
Selection: 
Selection: 
Selection: 
Selection: 
Selection: 
Selection: 


KeyboardInterrupt: 

KeyboardInterrupt: 

KeyboardInterrupt: 

...

KeyboardInterrupt: 

KeyboardInterrupt: 

KeyboardInterrupt: 

KeyboardInterrupt: 

KeyboardInterrupt: 

In [6]:
%%R
packageVersion('ggplot2')

[1] ‘2.2.1’


In [7]:
%%R
packageVersion('dplyr')

[1] ‘0.7.6’


In [8]:
%%R
packageVersion('tidyr')

[1] ‘0.8.1’


### Tools

#### Affichage coloré

In [9]:
# Termcolor
# OPTIONS  : bold, dark, underline, blink, reverse, concealed

text = colored('Hello, World!', 'red', attrs = ['blink'])
print(text)

text = colored('Hello, World!', 'red', attrs = ['dark'])
print(text)

text = colored('Hello, World!', 'red', attrs = ['underline'])
print(text)

text = colored('Hello, World!', 'red', attrs = ['bold'])
print(text)

text = colored('Hello, World!', 'red', attrs = ['concealed'])
print(text)

cprint('Hello, World!', 'green', 'on_red',attrs = ['reverse'])

Hello, World!
Hello, World!
Hello, World!
Hello, World!
Hello, World!
Hello, World!


#### Affichage lisible d'un dictionnaire complexe

In [10]:
# Display more readable dict
# SOURCE : https://stackoverflow.com/questions/3229419/how-to-pretty-print-nested-dictionaries
def pretty(d, indent=0):
    for key, value in d.items():
        print('\t' * indent + colored (str(key), "magenta"))
        if isinstance(value, type({})):
            pretty(value, indent+1)
        else:
            print('\t' * (indent+1) + str(value))

### Préparation de l'environnement pour l'expérience

#### Paramètres réservation

In [11]:
# Nom du job
jobname = ' '
# Nombre de noeuds
nodecount = 5
# Temps réservation
walltime = "3:0:0" 

# filters out Nantes's econome cluster
resources_selection = "-p \"cluster in ('ecotype','parasilo','grisou','uvb','paravance','genepi')\"" 

# Nancy
site = "nancy"

#Type de deploiement 
FILE_DEPLOY = True

#### Réservation

In [12]:
jobs = get_current_oar_jobs()
jobid = None
waiting_jobs = []
while jobs:
    j, site = jobs.pop()
    info = get_oar_job_info(j, site)
    if info['name'] == jobname:
        if info['state'] == 'Running':
            jobid = j
            print("A {} job is already running, using it. jobid is {}".format(jobname, jobid))
            break
        else:
            waiting_jobs.append(j)
if not jobid and not waiting_jobs:
    jobspec = OarSubmission(resources="/cluster=1/nodes={}".format(nodecount), walltime = walltime,
                            additional_options = resources_selection, job_type = "deploy", name = jobname)
    jobid, _ = oarsub([(jobspec, site)]).pop()
    print("New job submitted, jobid is {}".format(jobid))
elif not jobid:
    print("One or more {} jobs exist ({}) but are not running.\n"
          " Connect to the frontend to see what is happening, and/or run the cell again.".format(
          jobname, ", ".join([str(j) for j in waiting_jobs])))

A   job is already running, using it. jobid is 1600209


#### Récupération des infos sur les noeuds obtenus

###### Note : Si cette cellule met du temps à répondre, vérifier l'état de la réservation sur la frontale **oartstat -u username** ou via https://www.grid5000.fr/mediawiki/index.php/Status

In [13]:
nodes = get_oar_job_nodes(jobid)
nodes.sort(key = lambda n: n.address)
nodes

[Host('grisou-5.nancy.grid5000.fr'),
 Host('grisou-50.nancy.grid5000.fr'),
 Host('grisou-51.nancy.grid5000.fr'),
 Host('grisou-6.nancy.grid5000.fr'),
 Host('grisou-7.nancy.grid5000.fr')]

##### Déploiement de l'environnement : 2 options

###### Via fichier 

In [14]:
force_redeploy = False # set to True to force redeploying the OS on the nodes in the deployment section
environment_dsc_file = 'src/debian9-x64-bigdata-tutorial.yaml' # filename of the kadeploy environment file (YAML)

In [15]:
if (FILE_DEPLOY):
    deployment = Deployment(hosts = nodes, env_file = os.path.abspath(environment_dsc_file),
                        other_options = "-r ext4 --no-debug-mode")

    deploy_ok, deploy_failed = deploy(deployment, check_deployed_command = not force_redeploy,
                              stdout_handlers = [sys.stdout],
                              stderr_handlers = [sys.stderr])
else :
    deploy_ok, deploy_failed = deploy(Deployment(nodes, env_name = "debian9-x64-base",
                              other_options = "-r ext4 --no-debug-mode"),
                              stdout_handlers = [sys.stdout],
                              stderr_handlers = [sys.stderr])

In [16]:
print("Deployement status:\n* ok: {}\n* failed: {}".format(deploy_ok, deploy_failed))

Deployement status:
* ok: {'grisou-50.nancy.grid5000.fr', 'grisou-5.nancy.grid5000.fr', 'grisou-51.nancy.grid5000.fr', 'grisou-7.nancy.grid5000.fr', 'grisou-6.nancy.grid5000.fr'}
* failed: set()


#### Test : commande simple 'ls'

In [17]:
Remote_test = execo.action.Remote(cmd = 'ls',hosts = nodes, connection_params = None, process_args = None)
Remote_test.run().ok

True

#### Installation environnement/tools sur noeuds

In [18]:
if (not crashed):
    Remote_install = execo.action.Remote(cmd = 'apt-get install g++ libboost-all-dev && wget http://gforge.inria.fr/frs/download.php/latestfile/8/SimGrid-3.18.tar.gz && tar -xvf SimGrid-3.18.tar.gz && cd SimGrid-3.18 && cmake -DCMAKE_INSTALL_PREFIX=/usr/local -Denable_smpi=on -Denable_documentation=off && make -j && make check && make install -j',
                                     hosts = nodes,connection_params = {'user':'root'})
    Remote_install.run().ok

In [19]:
if (not crashed):
    Pajeng_install = execo.action.Remote(cmd='git clone git://github.com/schnorr/pajeng.git ; mkdir -p pajeng/build ; cd pajeng/build ; cmake .. ; make ; make install',hosts=nodes,connection_params={'user':'root'}).run().ok
    Pajeng_install

#### Version Simgrid

In [20]:
def remote_version(software):
    execo.action.Remote(cmd = 'touch version.txt &&' + str(software) + ' --version > version.txt'
                    , hosts = nodes, connection_params = {'user': 'root'}).run()

    version = ''

    for i in range(0, nodecount):
        execo.action.Get(hosts = nodes[i], remote_files = ['~/version.txt'],
                         local_location = './version-'
                                            + get_host_shortname(nodes[i]) + '.txt',
                         connection_params = {'user': 'root'}).run()
    
        version = version + execo.Process(cmd = 'cat ./version-'
                                                + get_host_shortname(nodes[i]) 
                                                + '.txt').run().stdout
        execo.Process(cmd = 'rm ./version-'
                            + get_host_shortname(nodes[i]) + '.txt').run()

    print(colored('VERSION : ' + str(software),"blue"), '\n' + version + '\n')
    return

remote_version('smpicc')
remote_version('g++')

VERSION : smpicc 
SimGrid version 3.18
SimGrid version 3.18
SimGrid version 3.18
SimGrid version 3.18
SimGrid version 3.18


VERSION : g++ 
g++ (Debian 6.3.0-18) 6.3.0 20170516
Copyright (C) 2016 Free Software Foundation, Inc.
This is free software; see the source for copying conditions.  There is NO
warranty; not even for MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.

g++ (Debian 6.3.0-18) 6.3.0 20170516
Copyright (C) 2016 Free Software Foundation, Inc.
This is free software; see the source for copying conditions.  There is NO
warranty; not even for MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.

g++ (Debian 6.3.0-18) 6.3.0 20170516
Copyright (C) 2016 Free Software Foundation, Inc.
This is free software; see the source for copying conditions.  There is NO
warranty; not even for MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.

g++ (Debian 6.3.0-18) 6.3.0 20170516
Copyright (C) 2016 Free Software Foundation, Inc.
This is free software; see the source for copying condit

#### Chemins (à configurer)

In [21]:
path_base = "/home/nezzine/Stage-POLARIS/SimGrid/examples/SMPI/" + experiment_name
path_src = path_base + '/src/'
path_rslt = path_base + '/results/'

#### Traitement des données pour les calculs de D et S

In [22]:
# Intialise tableau
def init_tab(num, elt) :
    D = [elt] * num
    return D

# Parsing the results
def parser(num_node,date_precise):
    with open( '/home/nezzine/Stage-POLARIS/SimGrid/examples/SMPI/Time_Bcast/results/'
               + date_precise.split('_')[0] + '/'
               + get_host_shortname(nodes[num_node]) + '_'
               + date_precise
               + '.txt') as f:
        return f.readlines()
    
# Converting and organizing data
def tab_conv(l, NPROCS, precision) :
    S = init_tab(NPROCS, None)
        
    # On récupère les données des fichiers
    # Un fichier contient des lignes telles que : From 0 -> S[0] : 0.0819526    
    for i in range(0, NPROCS) :
        line = l[i].split()
        S[int(line[1])] = round(float(line[5]), precision)
    return S

def delayer(num_node, NPROCS, date, precision):
    D = init_tab(NPROCS, 0.0)
    
    raw_data = parser(num_node, date)
    
    S = tab_conv(raw_data, NPROCS, precision)
    
    for p in range(0, NPROCS):
        D[p] = round(S[p] - min(S), precision)
    return [D, min(S)]

In [ ]:
# Example
# delayer(0,10,'2018-06-04_12:38',2)

## SIMULATION

#### Mise en place de l'environnement (fichiers src simulation...) sur noeuds

In [23]:
def setup() :
    Src_dir = execo.action.Remote(cmd = 'mkdir -p experiments_src',
                              hosts = nodes,
                              connection_params = {'user': 'root'})
    Src_get = execo.action.Put(hosts = nodes, local_files = [path_src
                                   + 'griffon.xml', path_src
                                   + 'griffon_hostfile.txt', path_src
                                   + 'broadcast.c', path_src 
                                   + 'Makefile'],
                                   remote_location = '~/experiments_src',
                                   connection_params = {'user': 'root'})
    Rslt_dir = \
        execo.Process(cmd='mkdir -p '
                  + path_rslt
                  + datetime.datetime.now().strftime('%Y-%m-%d'))

# On récup les src
    Src_dir.run().ok
    Src_get.run().ok
    Rslt_dir.run().ok


#### Défintion du thread pour parallélisation de la simulation

In [35]:
# Thread pour la simulation // opt.
class ParSimer(Thread):

    """Thread chargé simplement d'afficher une lettre dans la console."""
    
    # Paramètrage du thread
    def __init__(self,i,MIN,MAX,N,DELAY):
        Thread.__init__(self)
        self.MIN = MIN
        self.MAX = MAX
        self.N = N
        self.DELAY = DELAY
        self.i = i
    
    # Set la valeur du délai
    def set_delay(self,delay):
        self.DELAY = delay
    
    def get_delay(self):
        return self.DELAY
    
    def get_MIN(self):
        return self.MIN
    
    def run(self):
        """Code à exécuter pendant l'exécution du thread."""
        if (False): 
            print(
                get_host_shortname(nodes[self.i]) + " => " + str(self.i) + " NPROCS = " + str(NPROCS)
             + " MIN = " + str(self.MIN)
             + " MAX = " + str(self.MAX)
             + " N = " + str(self.N)
             + " DELAY = '" + self.DELAY + "'\n"
            )
       
        # make run sur toutes la machine dont le thread s'occupe avec ses paramètres
        execo.action.Remote(cmd ='cd ~/experiments_src && make && make run NPROCS='
                                  + str(NPROCS) + ' MIN='+ str(self.MIN) 
                                  + ' MAX=' + str(self.MAX) + ' N=' + str(self.N)
                                  + " DELAY='" + self.DELAY
                                  + "'" , 
                            hosts = nodes[self.i], 
                            connection_params = {'user':'root'}).run().ok


#### Conversion string < = > int pour manipulation de D & S

In [25]:
# Formate le tableau en string pour pouvoir etre passé en ligne de commande
def format_cmd(data):
    return (' '.join(str(e) for e in data))

# Formate le string en tableau d'int pour être manipulé 
def unformat_cmd(data):
    return list(map(float,data.split()))

#### Génération du nouvel état initial

In [26]:
def generate_Dprime(NPROCS,border_inf,border_sup,precision):
    # Variable pour le stockage du nouveau D
    new_Dprime = []
    
    if (border_inf == 0):
        for p in range(NPROCS):
            new_value = random.uniform(border_inf, border_sup[p])
            new_round_value = round(new_value, precision)
            new_Dprime.append(new_round_value)
    else : 
        for p in range(NPROCS):
            new_Dprime.append(round(random.uniform(border_inf[p], border_sup[p]), precision))
    return format_cmd(new_Dprime)

#### Code de la simulation

In [29]:
# SIMULATION
DEBUG = True
def simulation(N, NPROCS, fragment_size, precision, mode, catch_me):
    
    """Contrôle de la validité des paramètres"""
    # Taille du fragment ne peut être supérieure à la zone d'itération
    if (fragment_size > N): 
        raise ValueError("Fragment size cannot be superior to N")
        
    """Mise en place de l'environnement et des variables"""
    # Environnement
    setup() 
    
    # Dates: pour la gestion de fichiers (IMPORTANT pour lecture/écriture)
    date_precise = datetime.datetime.now().strftime('%Y-%m-%d_%H:%M')
    date = date_precise.split('_')[0]
    
    # Temps d'exécution total
    total_execution_time = 0
    
    # Tableau de threads
    machines = init_tab(nodecount, None)
      
    # position trajectoire cohérente courante
    t_curr = 0
    
    # D de la trajectorie cohérente courante
    D_curr = format_cmd(init_tab(NPROCS, 0.0))
    
    # Taille du dernier slot
    last_fragment_size = N % fragment_size
    
    # Nombre de fragments
    fragment_number = int((math.ceil(N / fragment_size)))
    
    # zone d'itérations à explorer
    To_explore = collections.deque()
    
    # Initialisation des zones à explorer D = '0...0' pour chaque zone T -> (Min d'itération , D initial)
    for i in range(fragment_number):
        To_explore.append((i * fragment_size, format_cmd(init_tab(NPROCS, 0.0))))

    # Round actuel
    curr_round = 0
    
    # Liste des trajectoires pour un temps t et un D donnée
    sim = OrderedDict()
    
    # Vrai si un état final a fusionné avec un état initial au moins une fois
    success = False 
    
    catch_me_ind = 0
    
    while(True):
        curr_round = curr_round + 1
        
        # Trajectoire cohérente complète trouvé : FIN DE SIMULATION
        if (t_curr >= N) :
            cprint ("Total time : " + str(total_execution_time) , "grey" , "on_yellow")
            cprint ("Success : " + str(success) , "grey" , "on_green")
            break;        
        if (len(To_explore) == 0):
            raise 
        # Il n'existe pas encore de trajectoire cohérente -> Nouveau round
        cprint("--------------------------------------------  ROUND :  " + str(curr_round) + "   --------------------------------------------\n","red", attrs=['reverse', 'blink'])
        
        # Zones restantes à explorer
        number_paths_To_explore = len(To_explore)
        
        # Nombre de tâches parallèles lançables
        number_launchable_tasks = min(nodecount, number_paths_To_explore)
        
        # Affichage des paramètres
        cprint ("  || LAUNCHING || \n","green", attrs=[ 'reverse', 'blink'])
        if (DEBUG): 
            cprint ( "TO EXPLORE : " , "blue")
            for key, value in (To_explore):
                print( colored( str(key), "green") + ' -> ' + str(value))
        
        """ Paramètrage des machines """
        
        # Soit j'ai plus de zone à explorer que de machines disponibles soit l'inverse
        for q in range(number_launchable_tasks):
            
            # On récupère la première zone à explorer
            parameters = To_explore.popleft()
            
            # MIN est le champ de gauche
            MIN = parameters[0]
            
            # MAX de la zone à explorer vaut le min + la taille du slot
            MAX = min (MIN + fragment_size, N)
            
            # D est le champ de droite
            delay = parameters[1]
            
            # Paramètrage des machines
            machines[q] = ParSimer(q, MIN, MAX, N, delay)
            #print("Machine " + str(q) + " -> MIN :" + str(MIN) + " MAX : " + str(MAX) + " D : "+ delay)   
                
        """ Simulation """  
        # Lancement de la simulation
        for q in range(number_launchable_tasks):
            machines[q].start()
            
        # Fin de simulation
        for q in range(number_launchable_tasks) :
            machines[q].join()
            # Récupération des résultats
            execo.action.Get(hosts=nodes[q],
                     remote_files=['~/experiments_src/bcast_results.txt'
                     ],
                     local_location= path_rslt
                     + date
                     + '/' + get_host_shortname(nodes[q]) + '_'
                     + date_precise + '.txt', connection_params={'user': 'root'
                     }).run().ok

            execo.action.Remote(cmd='pj_dump --ignore-incomplete-links ./experiments_src/Time_Bcast.trace > ./experiments_src/Time_Bcast.csv',hosts=nodes,connection_params={'user':'root'}).run()
            name = path_rslt + date + '/' + get_host_shortname(nodes[q]) + '_'+ date_precise
            execo.action.Get(hosts=nodes[q],
                     remote_files=['~/experiments_src/Time_Bcast.csv'
                     ],
                     local_location= path_rslt
                     + date
                     + '/' + get_host_shortname(nodes[q]) + '_'
                     + date_precise + '.csv', connection_params={'user': 'root'
                     }).run().ok
            

            execo.action.Remote(cmd='grep State'+ str(name)+'.csv > ./Time_Bcast.state.csv',hosts=nodes,connection_params={'user': 'root'
                     })
            execo.action.Remote(cmd='grep Link'+ str(name)+'.csv > ./Time_Bcast.link.csv',hosts=nodes,connection_params={'user': 'root'
                     })
            execo.action.Remote(cmd='grep Container'+ str(name)+'.csv > ./Time_Bcast.container.csv',hosts=nodes,connection_params={'user': 'root'
                     })
            execo.action.Remote(cmd='grep Variable'+ str(name)+'.csv > ./Time_Bcast.variable.csv',hosts=nodes,connection_params={'user': 'root'
                     })
            execo.action.Get(hosts=nodes[q],
                     remote_files=['~/experiments_src/Time_Bcast.*'
                     ],
                     local_location = path_base, connection_params={'user': 'root'
                     }).run().ok
            
            """           
            execo.Process(cmd='touch ./Time_Bcast.state.csv').run()
            execo.Process(cmd='grep State'+ str(name)+'.csv > Time_Bcast.state.csv').run()
            execo.Process(cmd='touch ./Time_Bcast.link.csv').run()
            execo.Process(cmd='grep Link'+ str(name)+'.csv > Time_Bcast.link.csv').run()
            execo.Process(cmd='touch ./Time_Bcast.container.csv').run()
            execo.Process(cmd='grep Container'+ str(name)+'.csv > Time_Bcast.container.csv').run()
            execo.Process(cmd='touch ./Time_Bcast.variable.csv').run()
            execo.Process(cmd='grep Variable'+ str(name)+'.csv > Time_Bcast.variable.csv').run()
            
           
           #subprocess.Popen(['bash', '-c', '. greper.sh; grepping',name])
            subprocess.call(["grep", "State", name, ".csv > Time_Bcast.state.csv"])
            
            %R library(ggplot2)
            %R df_state = read.csv("./Time_Bcast.csv", header = F, strip.white=T)
            %R names(df_state) = c("Type", "Rank", "Container", "Start", "End", "Duration", "Level", "State"); 
            %R df_state = df_state[!(names(df_state) %in% c("Type","Container","Level"))]
            %R df_state$Rank = as.numeric(gsub("rank-","",df_state$Rank))
            %R head(df_state)
            %R str(df_state)
            """ 
          
        """ Analyse des résultats"""    
        # Traitement des données
        for q in range(number_launchable_tasks):
            # On récupère les paramètres des machines
            t = machines[q].get_MIN()
            D = machines[q].get_delay()
            
            # Calcul du délai
            # On récupère D et S
            raw_data = delayer(q, NPROCS, date_precise,precision)
            
            # Filtre D : Calcul du délai
            Dprime = format_cmd(raw_data[0])
            
            #Filte S : Calcul du temps d'éxécution total 
            T = raw_data[1]
            
            # Ajout dans ma table (Dprime, round, machine qui l'a calculé, temps)
            sim.setdefault(t,{}).update({D:(Dprime,curr_round,q,T)})
            MAX = min (t + fragment_size, N)
        
        # Affichage des paramètres
        print ( colored ("T_curr : " , "yellow") , str(t_curr))
        if (DEBUG) :
            print ( colored ("D_curr : " , "yellow") , str(D_curr))
            print ( colored ("Dprime : ", "yellow") , str(Dprime))
        print ( colored ("total execution time : ", "red") , str(total_execution_time) + "\n") 
        
        merged_paths = 0
        # Calcul de la trajectoire cohérente
        while (t_curr < N and t_curr in sim and D_curr in sim[t_curr]):
            merged_paths += 1
            # Update le temps d'exécution
            total_execution_time += sim[t_curr][D_curr][3]
            
            # Update du temps d'exécution dans le dernier fragment
            if (t_curr + fragment_size >= N) : total_execution_time += max(unformat_cmd(sim[t_curr][D_curr][0]))
            
            # Update des t_curr et D_curr
            D_curr = sim[t_curr][D_curr][0]
            t_curr = min(t_curr + fragment_size, N)
        if (merged_paths > 1) : 
            cprint("****** SUCCESS : " + str(merged_paths), attrs=['reverse', 'bold'])
            success = True 
        
        # Affichage des résultats
        cprint ("\n  || RESULTS || \n","red", attrs=[ 'reverse', 'blink'])
        if (DEBUG):
            cprint ( "TO EXPLORE : " , "blue")
            for key, value in (To_explore):
                print( colored( str(key), "green") + ' -> ' + str(value)) 
            pretty (sim) 
        print ( colored ("T_curr : " , "yellow", attrs=[ 'bold']), str(t_curr))
        
        if (DEBUG):
            print ( colored ("D_curr : " , "yellow", attrs=[ 'bold']), str(D_curr))
            print ( colored ("Dprime : ", "yellow", attrs=[ 'bold']) , str(Dprime))
            
        print ( colored ("total execution time : ", "red", attrs=[ 'bold']) , str(total_execution_time) + "\n") 
        
        
        """ Nouveau paramètrages """
        cprint("  || ANALYSIS || \n","magenta", attrs=[ 'reverse', 'blink'])
        while (To_explore and To_explore[0][0] <= t_curr):
            To_explore.popleft()
        
        for q in reversed(range(number_launchable_tasks)):
            t = machines[q].get_MIN()
            D = machines[q].get_delay()
            
            MAX = min(t + fragment_size, N)
            Dprime = sim[t][D][0]
           
            # Zone valide
            if(MAX < N):
                # Zone pas encore relié à la trajectoire initiale
                if (MAX > t_curr):
                    caught = False
                # Ajout dans les zones à explorer du nouveau point de départ à exploiter en fonction du mode
                    # Test catch me sur 2^catch_me_ind round
                    if (catch_me and 1 << catch_me_ind == curr_round):
                        catch_me_ind += 1
                        try :
                            caught = Dprime in sim[MAX]
                        except KeyError:
                            pass 
                       
                    if (not catch_me or not caught):
                        borders = unformat_cmd(Dprime)
                        double_Dprime = [(2*(x)) for x in borders]
                      
                        # Bornes pour le random 
                        border_inf = 0
                        border_sup = double_Dprime
                        if (mode == "RAND_SUP") : 
                            border_sup = borders
                            Dprime =  generate_Dprime(NPROCS, border_inf, border_sup,precision)
                        elif (mode == "RAND_INF") : 
                            border_inf = borders
                            Dprime = generate_Dprime(NPROCS, border_inf, border_sup,precision)
                        elif (mode == "RAND") : 
                            Dprime =  generate_Dprime(NPROCS, border_inf, border_sup,precision)
                        if (DEBUG) : print("["+str(MAX) +"] Generated " + str(mode) + " Dprime : " + str(Dprime))
                    # Mode fix implicite : append sans modification des valeurs MAX et Dprime    
                    To_explore.appendleft((MAX, Dprime))
        
        if (t_curr != N):
            To_explore.appendleft((t_curr, D_curr))
        if (DEBUG):
            cprint ( "TO EXPLORE : " , "blue")
            for key, value in (To_explore):
                print( colored( str(key), "green") + ' -> ' + str(value))
        

## SIMULATION

In [31]:
# Nbr pcs
NPROCS = 10
    
# Nbr itérations
N = 100

# taille paquet d'itérations
fragment_size = 10

precision = 4

# mode de génération de l'état initial à chaque round
mode_opt = ["FIX","RAND","RAND_INF","RAND_SUP"]
mode = mode_opt[1]

catch_me = False



# Lancement de la simulation
simulation(N,NPROCS,fragment_size,precision,mode,catch_me)

--------------------------------------------  ROUND :  1   --------------------------------------------

  || LAUNCHING || 

TO EXPLORE : 
0 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
10 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
20 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
30 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
40 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
50 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
60 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
70 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
80 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
90 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
grisou-5 => 0 NPROCS = 10 MIN = 0 MAX = 10 N = 100 DELAY = '0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0'

grisou-50 => 1 NPROCS = 10 MIN = 10 MAX = 20 N = 100 DELAY = '0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0'

grisou-51 => 2 NPROCS = 10 MIN = 20 MAX = 30 N = 100 DELAY = '0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0'

grisou-6 => 3 NPROCS = 10 MIN = 30 MAX = 40 N = 100 DELAY = '0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0

T_curr :  20
D_curr :  0.0015 0.0023 0.0029 0.0028 0.0036 0.0036 0.0042 0.0023 0.0029 0.0
Dprime :  0.0014 0.0021 0.0027 0.0029 0.0037 0.0037 0.0043 0.0023 0.0029 0.0
total execution time :  0.026099999999999998


  || RESULTS || 

TO EXPLORE : 
50 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
60 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
70 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
80 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
90 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
0
	0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
		('0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 1, 0, 0.013)
10
	0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0
		('0.0015 0.0023 0.0029 0.0028 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 2, 0, 0.0131)
	0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
		('0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 1, 1, 0.013)
20
	0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
		('0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029

T_curr :  40
D_curr :  0.0015 0.0023 0.0029 0.0028 0.0036 0.0036 0.0042 0.0023 0.0029 0.0
Dprime :  0.0015 0.0024 0.0031 0.0034 0.0042 0.0042 0.0048 0.0024 0.003 0.0
total execution time :  0.0523


  || RESULTS || 

TO EXPLORE : 
50 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
60 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
70 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
80 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
90 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
0
	0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
		('0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 1, 0, 0.013)
10
	0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0
		('0.0015 0.0023 0.0029 0.0028 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 2, 0, 0.0131)
	0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
		('0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 1, 1, 0.013)
20
	0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
		('0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 1, 2, 0.

T_curr :  60
D_curr :  0.0015 0.0023 0.0029 0.0028 0.0036 0.0036 0.0042 0.0023 0.0029 0.0
Dprime :  0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0
total execution time :  0.0785


  || RESULTS || 

TO EXPLORE : 
80 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
90 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
0
	0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
		('0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 1, 0, 0.013)
10
	0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0
		('0.0015 0.0023 0.0029 0.0028 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 2, 0, 0.0131)
	0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
		('0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 1, 1, 0.013)
20
	0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
		('0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 1, 2, 0.013)
	0.0012 0.0016 0.0004 0.0003 0.0049 0.001 0.0013 0.0018 0.0047 0.0
		('0.0015 0.0024 0.0031 0.0033 0.0042 0.0042 0.0048 0.0023 0.002

T_curr :  70
D_curr :  0.0015 0.0023 0.0029 0.0028 0.0036 0.0036 0.0042 0.0023 0.0029 0.0
Dprime :  0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0
total execution time :  0.0916


  || RESULTS || 

TO EXPLORE : 
90 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
0
	0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
		('0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 1, 0, 0.013)
10
	0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0
		('0.0015 0.0023 0.0029 0.0028 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 2, 0, 0.0131)
	0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
		('0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 1, 1, 0.013)
20
	0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
		('0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 1, 2, 0.013)
	0.0012 0.0016 0.0004 0.0003 0.0049 0.001 0.0013 0.0018 0.0047 0.0
		('0.0015 0.0024 0.0031 0.0033 0.0042 0.0042 0.0048 0.0023 0.0029 0.0', 2, 1, 0.0116)
	0.0015 0.0023 0.0029 0.

T_curr :  80
D_curr :  0.0015 0.0023 0.0029 0.0028 0.0036 0.0036 0.0042 0.0023 0.0029 0.0
Dprime :  0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0
total execution time :  0.1047


  || RESULTS || 

TO EXPLORE : 
0
	0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
		('0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 1, 0, 0.013)
10
	0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0
		('0.0015 0.0023 0.0029 0.0028 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 2, 0, 0.0131)
	0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
		('0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 1, 1, 0.013)
20
	0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
		('0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 1, 2, 0.013)
	0.0012 0.0016 0.0004 0.0003 0.0049 0.001 0.0013 0.0018 0.0047 0.0
		('0.0015 0.0024 0.0031 0.0033 0.0042 0.0042 0.0048 0.0023 0.0029 0.0', 2, 1, 0.0116)
	0.0015 0.0023 0.0029 0.0028 0.0036 0.0036 0.0042 0.0023 0.0029 0.0
		

T_curr :  90
D_curr :  0.0015 0.0023 0.0029 0.0028 0.0036 0.0036 0.0042 0.0023 0.0029 0.0
Dprime :  0.0015 0.0023 0.0029 0.0028 0.0036 0.0036 0.0042 0.0023 0.0029 0.0
total execution time :  0.1178


  || RESULTS || 

TO EXPLORE : 
0
	0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
		('0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 1, 0, 0.013)
10
	0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0
		('0.0015 0.0023 0.0029 0.0028 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 2, 0, 0.0131)
	0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
		('0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 1, 1, 0.013)
20
	0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
		('0.0014 0.0023 0.0029 0.0027 0.0036 0.0036 0.0042 0.0023 0.0029 0.0', 1, 2, 0.013)
	0.0012 0.0016 0.0004 0.0003 0.0049 0.001 0.0013 0.0018 0.0047 0.0
		('0.0015 0.0024 0.0031 0.0033 0.0042 0.0042 0.0048 0.0023 0.0029 0.0', 2, 1, 0.0116)
	0.0015 0.0023 0.0029 0.0028 0.0036 0.0036 0.0042 0.0023 0.0029 0.0
		

In [36]:
# Nbr pcs
NPROCS = 1000
    
# Nbr itérations
N = 100

# taille paquet d'itérations
fragment_size = 10

precision = 4

# mode de génération de l'état initial à chaque round
mode_opt = ["FIX","RAND","RAND_INF","RAND_SUP"]
mode = mode_opt[1]

catch_me = False

# Lancement de la simulation
simulation(N,NPROCS,fragment_size,precision,mode,catch_me)

--------------------------------------------  ROUND :  1   --------------------------------------------

  || LAUNCHING || 

TO EXPLORE : 
0 -> 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 

T_curr :  0
D_curr :  0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.

T_curr :  10
D_curr :  0.0711 0.068 0.0724 0.0724 0.0757 0.0749 0.0769 0.0769 0.0777 0.0 0.0135 0.0202 0.0271 0.0183 0.0252 0.0307 0.0373 0.0256 0.0321 0.0345 0.0412 0.0321 0.0387 0.04 0.0461 0.0281 0.0345 0.0352 0.0419 0.038 0.0388 0.0391 0.0404 0.0358 0.037 0.037 0.0378 0.037 0.0379 0.0379 0.039 0.0175 0.019 0.019 0.0198 0.019 0.0208 0.0197 0.0203 0.019 0.0202 0.0203 0.0216 0.0202 0.0211 0.0211 0.022 0.0257 0.0322 0.0353 0.0431 0.0455 0.0502 0.0502 0.0542 0.0428 0.0479 0.0479 0.0522 0.0479 0.0522 0.0522 0.0561 0.0328 0.0378 0.0378 0.0428 0.0378 0.0428 0.0428 0.0479 0.0378 0.0428 0.0428 0.0479 0.0428 0.0479 0.0479 0.0522 0.0378 0.0428 0.0428 0.0501 0.0473 0.0537 0.0537 0.0597 0.0596 0.0655 0.0655 0.0706 0.0655 0.0706 0.0706 0.0743 0.0572 0.0631 0.0631 0.0687 0.0631 0.0687 0.0687 0.073 0.0631 0.0687 0.0687 0.073 0.0687 0.073 0.073 0.076 0.0644 0.0658 0.0658 0.0664 0.0659 0.0677 0.0677 0.0684 0.0661 0.0687 0.0687 0.0695 0.0687 0.071 0.071 0.0721 0.0201 0.0218 0.0218 0.0224 0.0218 0.0228

T_curr :  20
D_curr :  0.1338 0.1338 0.137 0.1326 0.1362 0.1362 0.1386 0.1367 0.1392 0.1392 0.1407 0.129 0.1333 0.1333 0.1367 0.1335 0.1378 0.1378 0.14 0.0 0.0018 0.0026 0.0032 0.0037 0.0053 0.006 0.0067 0.0074 0.008 0.0092 0.0099 0.0105 0.0112 0.0115 0.0121 0.0103 0.0109 0.0116 0.0123 0.012 0.0128 0.0128 0.0135 0.0115 0.0122 0.0125 0.0131 0.0132 0.0141 0.0141 0.0147 0.0034 0.0042 0.0042 0.0049 0.005 0.0058 0.0059 0.0065 0.005 0.0093 0.0124 0.0355 0.0432 0.0492 0.0559 0.0625 0.0684 0.0735 0.0746 0.0796 0.0844 0.0892 0.0937 0.0979 0.0787 0.0834 0.0881 0.0928 0.0892 0.0938 0.098 0.1016 0.0322 0.038 0.0388 0.0448 0.0503 0.0559 0.0559 0.0614 0.0493 0.0571 0.0612 0.0677 0.0716 0.0778 0.0778 0.0841 0.0808 0.0872 0.0921 0.0985 0.1049 0.111 0.1171 0.1227 0.1279 0.1323 0.1323 0.136 0.1323 0.136 0.136 0.1385 0.1265 0.1318 0.1318 0.1356 0.1318 0.1356 0.1362 0.137 0.1326 0.1338 0.1338 0.1344 0.1338 0.1346 0.1346 0.1359 0.1326 0.1343 0.1343 0.1355 0.1343 0.1352 0.1352 0.136 0.1343 0.1357 0.1357 0.1

T_curr :  30
D_curr :  0.1844 0.1836 0.1875 0.1875 0.191 0.1848 0.1886 0.1886 0.1918 0.1886 0.1918 0.1918 0.1937 0.1886 0.1918 0.1918 0.1937 0.1918 0.1944 0.1944 0.1959 0.1953 0.1966 0.1966 0.1974 0.1967 0.1997 0.1997 0.2011 0.0 0.0013 0.002 0.0028 0.0034 0.0041 0.0044 0.0051 0.0059 0.0067 0.0076 0.0084 0.009 0.0099 0.0099 0.0105 0.0074 0.0083 0.0091 0.0099 0.0105 0.0113 0.0113 0.012 0.0114 0.0122 0.0122 0.0128 0.0127 0.0135 0.0135 0.0142 0.0041 0.0204 0.0267 0.0316 0.037 0.0421 0.0463 0.0514 0.0524 0.0567 0.0597 0.0658 0.0737 0.0841 0.0898 0.0944 0.0993 0.1042 0.1051 0.11 0.1113 0.1159 0.1201 0.1243 0.1042 0.1093 0.1093 0.1141 0.1093 0.1141 0.1141 0.1221 0.04 0.0448 0.0478 0.0528 0.0536 0.0575 0.0584 0.0601 0.0636 0.0685 0.0755 0.0841 0.1015 0.1155 0.1353 0.1486 0.1546 0.1605 0.1661 0.1716 0.1767 0.1815 0.1857 0.1894 0.1922 0.1948 0.1948 0.1967 0.1956 0.1983 0.1983 0.1994 0.1738 0.1756 0.1756 0.1763 0.1756 0.1765 0.1765 0.1771 0.1756 0.1768 0.1768 0.1774 0.1768 0.1776 0.1776 0.1783 0.

...

T_curr :  50
D_curr :  0.2376 0.2358 0.2371 0.2371 0.2378 0.2371 0.238 0.238 0.2386 0.2277 0.2297 0.2297 0.2309 0.2297 0.231 0.231 0.232 0.2297 0.2311 0.2311 0.232 0.2311 0.2321 0.2321 0.2327 0.2297 0.2313 0.2313 0.2323 0.2394 0.2441 0.2475 0.2519 0.2548 0.2591 0.2591 0.2616 0.2604 0.2642 0.2642 0.2652 0.2654 0.269 0.269 0.27 0.2693 0.2707 0.2707 0.2716 0.0 0.0013 0.002 0.0028 0.0033 0.004 0.0043 0.0051 0.0066 0.0072 0.0078 0.0087 0.0092 0.0101 0.0101 0.0108 0.0114 0.0142 0.0164 0.0194 0.02 0.023 0.0249 0.0282 0.0329 0.0394 0.0429 0.0465 0.0496 0.054 0.056 0.058 0.0587 0.0601 0.0602 0.061 0.0607 0.0615 0.0615 0.0621 0.0606 0.0619 0.0619 0.067 0.0676 0.0684 0.0695 0.0704 0.0713 0.0721 0.0729 0.0738 0.0744 0.0752 0.0752 0.0758 0.0754 0.0762 0.0763 0.078 0.0828 0.0884 0.1038 0.1153 0.1255 0.1389 0.1699 0.1851 0.1924 0.198 0.2032 0.2083 0.2215 0.2266 0.2283 0.2333 0.2358 0.241 0.2408 0.2455 0.2443 0.249 0.2485 0.2527 0.2485 0.2526 0.2526 0.2561 0.2485 0.2526 0.2526 0.2564 0.2526 0.2558 0.2

T_curr :  60
D_curr :  0.2566 0.2566 0.2572 0.2543 0.2557 0.2557 0.2564 0.2557 0.2566 0.2566 0.2572 0.2557 0.2573 0.2573 0.2579 0.2573 0.2581 0.2581 0.2587 0.2524 0.2539 0.2539 0.2545 0.2539 0.2548 0.2548 0.2554 0.2539 0.2545 0.2599 0.2645 0.2599 0.2645 0.2645 0.269 0.2584 0.2631 0.2631 0.2677 0.2704 0.2739 0.2776 0.2799 0.2812 0.282 0.282 0.2846 0.2864 0.2888 0.2888 0.2902 0.2868 0.2892 0.29 0.2913 0.2881 0.2899 0.2903 0.2914 0.0 0.0017 0.0024 0.0031 0.0038 0.0045 0.0048 0.0056 0.0069 0.009 0.0098 0.0122 0.0135 0.0156 0.0191 0.0243 0.0272 0.0298 0.032 0.0355 0.0373 0.0384 0.0391 0.0401 0.041 0.0418 0.0427 0.0436 0.0442 0.0451 0.0451 0.0458 0.0452 0.0469 0.0479 0.0489 0.0498 0.0506 0.0506 0.0513 0.0515 0.0522 0.0526 0.0534 0.054 0.0548 0.0548 0.0554 0.056 0.0567 0.0575 0.0618 0.0739 0.0825 0.0904 0.1006 0.1251 0.1367 0.1437 0.1501 0.1545 0.1584 0.1756 0.1872 0.1916 0.1963 0.2002 0.2083 0.2158 0.2227 0.228 0.2343 0.2338 0.2403 0.2463 0.252 0.2576 0.2629 0.2675 0.2714 0.2748 0.2773 0.280

2018-07-05 02:49:38,166 WARNING: terminated: <SshProcess('pj_dump --ignore-incomplete-links ./experiments_src/Time_Bcast.trace > ./experiments_src/Time_Bcast.csv', Host('grisou-6.nancy.grid5000.fr'), connection_params={'user': 'root'}, name=pj_dump --ignore-incomplete-links ./..., started=True, start_date=2018-07-05 02:49:37+02:00, ended=True, end_date=2018-07-05 02:49:38+02:00, killed=False, error=False, error_reason=None, timeouted=False, expect_fail=False, write_error=False, exit_code=34304, ok=False, pid=21118, real cmd=('ssh', '-tt', '-o', 'BatchMode=yes', '-o', 'PasswordAuthentication=no', '-o', 'StrictHostKeyChecking=no', '-o', 'UserKnownHostsFile=/dev/null', '-o', 'ConnectTimeout=20', '-o', 'User=root', 'grisou-6.nancy.grid5000.fr', 'pj_dump --ignore-incomplete-links ./experiments_src/Time_Bcast.trace > ./experiments_src/Time_Bcast.csv'))>
stdout:
terminate called after throwing an instance of 'std::out_of_range'
  what():  vector::_M_range_check: __n (which is 3) >= this->size

2018-07-05 02:49:51,642 WARNING: terminated: <SshProcess('pj_dump --ignore-incomplete-links ./experiments_src/Time_Bcast.trace > ./experiments_src/Time_Bcast.csv', Host('grisou-6.nancy.grid5000.fr'), connection_params={'user': 'root'}, name=pj_dump --ignore-incomplete-links ./..., started=True, start_date=2018-07-05 02:49:51+02:00, ended=True, end_date=2018-07-05 02:49:51+02:00, killed=False, error=False, error_reason=None, timeouted=False, expect_fail=False, write_error=False, exit_code=34304, ok=False, pid=21187, real cmd=('ssh', '-tt', '-o', 'BatchMode=yes', '-o', 'PasswordAuthentication=no', '-o', 'StrictHostKeyChecking=no', '-o', 'UserKnownHostsFile=/dev/null', '-o', 'ConnectTimeout=20', '-o', 'User=root', 'grisou-6.nancy.grid5000.fr', 'pj_dump --ignore-incomplete-links ./experiments_src/Time_Bcast.trace > ./experiments_src/Time_Bcast.csv'))>
stdout:
terminate called after throwing an instance of 'std::out_of_range'
  what():  vector::_M_range_check: __n (which is 2) >= this->size

T_curr :  90
D_curr :  0.3104 0.3021 0.3033 0.3039 0.3046 0.3038 0.3048 0.3048 0.3054 0.3047 0.3062 0.3062 0.3069 0.3062 0.3071 0.3071 0.3077 0.2811 0.2828 0.2828 0.2835 0.2828 0.2837 0.2837 0.2843 0.2828 0.2839 0.2839 0.2845 0.284 0.2849 0.2849 0.2855 0.2829 0.2844 0.2844 0.2851 0.2844 0.2853 0.2853 0.2859 0.2844 0.287 0.287 0.2878 0.2871 0.2894 0.2894 0.2902 0.2811 0.2826 0.2826 0.2832 0.2826 0.2834 0.2834 0.284 0.2827 0.2836 0.2836 0.2891 0.2882 0.2924 0.2924 0.2961 0.2866 0.291 0.291 0.2948 0.2914 0.2952 0.2993 0.3027 0.3041 0.3058 0.3058 0.3068 0.3078 0.3095 0.3095 0.3102 0.3077 0.3096 0.3096 0.3112 0.3126 0.3153 0.3153 0.3167 0.0 0.0013 0.0019 0.0029 0.0036 0.0042 0.0047 0.0055 0.0064 0.0071 0.008 0.0089 0.0096 0.0106 0.0106 0.0112 0.0091 0.0101 0.0111 0.012 0.0131 0.0138 0.0144 0.0152 0.0188 0.0224 0.0336 0.0396 0.0446 0.0479 0.0506 0.0519 0.0605 0.0683 0.0691 0.07 0.0709 0.0737 0.0775 0.08 0.0835 0.0854 0.086 0.0875 0.0894 0.0944 0.0968 0.1125 0.1165 0.1221 0.1262 0.1314 0.1381

#### Publication des résultats sur GitHub : https://github.com/HooBaeBoo/Stage-POLARIS

In [37]:
%%bash -s $experiment_name $site
git add .
git commit -m 'Automatic results update : '"$1"' --- '"$2 ""Restructuration + Comment + pj_dump + Intégration R (Started->ggplot2)"

[master c7ccaa4] Automatic results update : Time_Bcast --- None Restructuration + Comment + pj_dump + Intégration R (Started->ggplot2)
 Committer: Najwa Ez Zine <nezzine@fnancy>
Your name and email address were configured automatically based
on your username and hostname. Please check that they are accurate.
You can suppress this message by setting them explicitly. Run the
following command and follow the instructions in your editor to edit
your configuration file:

    git config --global --edit

After doing this, you may fix the identity used for this commit with:

    git commit --amend --reset-author

 127 files changed, 203725 insertions(+), 86 deletions(-)
 create mode 100644 SimGrid/examples/SMPI/Time_Bcast/Time_Bcast.csv
 create mode 100644 SimGrid/examples/SMPI/Time_Bcast/Time_Bcast.trace
 delete mode 100644 SimGrid/examples/SMPI/Time_Bcast/is_64_small.link.csv
 delete mode 100644 SimGrid/examples/SMPI/Time_Bcast/is_64_small.state.csv
 delete mode 100644 SimGrid/examples/SMPI/

#### Fin d'expérience : suppression du job

In [ ]:
oardel([(jobid,site)])

### Zone Test (à ignorer)

In [12]:
sortie = execo.Process(cmd='ls').run().stdout
execo.Process(cmd = 'echo '+str(sortie)+' >> test10').run()

Process('echo is_64_small.container.csv\nis_64_small.link.csv\nis_64_small.state.csv\nis_64_small.variable.csv\nresults\nR tutorial.ipynb\nsrc\ntest10\nTime Broadcast.ipynb\n >> test10')

In [19]:
execo.action.Remote(cmd = 'touch helllllllllllllllllllo', hosts = 'localhost').run()

Remote('touch helllllllllllllllllllo', [Host('localhost')])